# Upload the BEANS sc recordings to HF

#### 1. Download the recordings the way BEANS do it on their [GitHub](https://github.com/earthspecies/beans)

First we will navigate into the mounted data_birdset folder to download the temporary files from the Repo their and install wget & unzip as they are not on the university bash.

In [1]:
%cd '../../../../../data_birdset/beans'
!pwd
!sudo apt install wget
!sudo apt install unzip

/workspace/data_birdset/beans
/workspace/data_birdset/beans


/workspace/.venv/lib/python3.10/site-packages/IPython/core/magics/osm.py:417: UserWarning: This is now an optional IPython functionality, setting dhist requires you to install the `pickleshare` library.
  self.shell.db['dhist'] = compress_dhist(dhist)[-100:]


Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
wget is already the newest version (1.21.2-2ubuntu1).
0 upgraded, 0 newly installed, 0 to remove and 49 not upgraded.
Reading package lists... Done
Building dependency tree... Done
Reading state information... Done
unzip is already the newest version (6.0-26ubuntu3.2).
0 upgraded, 0 newly installed, 0 to remove and 49 not upgraded.


Then we will run their script to download the metadata and recordings to have the same splits.

In [2]:
# Their script:
from pathlib import Path
import pandas as pd
from plumbum import local, FG

local['mkdir']['-p', 'data/speech_commands']()
local['wget']['http://download.tensorflow.org/data/speech_commands_v0.02.tar.gz', '-O', 'data/speech_commands/speech_commands_v0.02.tar.gz'] & FG
local['tar']['zxvf', 'data/speech_commands/speech_commands_v0.02.tar.gz', '-C', 'data/speech_commands/'] & FG

all_list = set()
for fn in Path('data/speech_commands').glob('*/*.wav'):
    if '_background_noise_' in str(fn):
        continue
    fn = '/'.join(str(fn).split('/')[-2:])
    all_list.add(fn)


testing_list = set()
with open('data/speech_commands/testing_list.txt') as f:
    for line in f:
        testing_list.add(line.strip())

validation_list = set()
with open('data/speech_commands/validation_list.txt') as f:
    for line in f:
        validation_list.add(line.strip())

training_list = all_list - validation_list - testing_list
training_list_low = [fn for i, fn in enumerate(sorted(training_list)) if i % 100 == 0]

def _to_df(lst):
    data = []
    for fn in lst:
        label = fn.split('/')[0]
        path = f"data/speech_commands/{fn}"
        data.append({'path': path, 'label': label})

    return pd.DataFrame.from_dict(data)

_to_df(sorted(training_list)).to_csv('data/speech_commands/train.csv')
_to_df(sorted(training_list_low)).to_csv('data/speech_commands/train-low.csv')
_to_df(sorted(validation_list)).to_csv('data/speech_commands/valid.csv')
_to_df(sorted(testing_list)).to_csv('data/speech_commands/test.csv')

--2024-04-08 12:48:39--  http://download.tensorflow.org/data/speech_commands_v0.02.tar.gz
Resolving download.tensorflow.org (download.tensorflow.org)... 142.250.184.251, 216.58.206.91, 142.250.186.91, ...
Connecting to download.tensorflow.org (download.tensorflow.org)|142.250.184.251|:80... connected.
HTTP request sent, awaiting response... 200 OK
Length: 2428923189 (2.3G) [application/gzip]
Saving to: ‘data/speech_commands/speech_commands_v0.02.tar.gz’

     0K .......... .......... .......... .......... ..........  0%  459K 86m9s
    50K .......... .......... .......... .......... ..........  0%  459K 86m9s
   100K .......... .......... .......... .......... ..........  0% 1.35M 66m56s
   150K .......... .......... .......... .......... ..........  0% 1.27M 57m48s
   200K .......... .......... .......... .......... ..........  0% 1.37M 51m53s
   250K .......... .......... .......... .......... ..........  0% 1.68M 47m4s
   300K .......... .......... .......... .......... ..........  

./
./eight/
./eight/1b88bf70_nohash_0.wav
./eight/798f702a_nohash_2.wav
./eight/b12bef84_nohash_1.wav
./eight/05b2db80_nohash_1.wav
./eight/b66f4f93_nohash_5.wav
./eight/750e3e75_nohash_0.wav
./eight/3852fca2_nohash_0.wav
./eight/5ac04a92_nohash_0.wav
./eight/778a4a01_nohash_0.wav
./eight/61e50f62_nohash_0.wav
./eight/0cb74144_nohash_2.wav
./eight/17c94b23_nohash_0.wav
./eight/037c445a_nohash_1.wav
./eight/3d794813_nohash_4.wav
./eight/11321027_nohash_0.wav
./eight/06f6c194_nohash_4.wav
./eight/b97c9f77_nohash_1.wav
./eight/10467b06_nohash_1.wav
./eight/321aba74_nohash_0.wav
./eight/d3831f6a_nohash_3.wav
./eight/d3831f6a_nohash_4.wav
./eight/baf01c1f_nohash_0.wav
./eight/472b8045_nohash_1.wav
./eight/64e48f55_nohash_1.wav
./eight/ab46af55_nohash_2.wav
./eight/6969e51a_nohash_0.wav
./eight/48bdc11c_nohash_0.wav
./eight/2e75d37a_nohash_1.wav
./eight/cb2929ce_nohash_4.wav
./eight/a6285644_nohash_2.wav
./eight/f30285c8_nohash_2.wav
./eight/01b4757a_nohash_0.wav
./eight/ea1f888c_nohash_0.wa

#### 2. Convert to HF format

In [3]:
from datasets import Dataset, Audio
import pandas as pd

def load_dataset(split_name):
    df = pd.read_csv(f'data/speech_commands/{split_name}.csv')
    dataset = Dataset.from_pandas(df)
    dataset = dataset.cast_column('path', Audio())
    return dataset

splits = ['train', 'train-low', 'valid', 'test']
datasets = {split: load_dataset(split) for split in splits}
datasets['train_low'] = datasets.pop('train-low') # Rename split from train-low to train_low as HF does not accept -
for split, dataset in datasets.items():
    print(dataset[0])

{'Unnamed: 0': 0, 'path': {'path': 'data/speech_commands/backward/0165e0e8_nohash_0.wav', 'array': array([-0.06576538, -0.07092285, -0.07531738, ..., -0.06997681,
       -0.07305908, -0.07043457]), 'sampling_rate': 16000}, 'label': 'backward'}
{'Unnamed: 0': 0, 'path': {'path': 'data/speech_commands/backward/067f61e2_nohash_0.wav', 'array': array([-0.00064087, -0.00018311, -0.00036621, ...,  0.0039978 ,
        0.00540161,  0.00592041]), 'sampling_rate': 16000}, 'label': 'backward'}
{'Unnamed: 0': 0, 'path': {'path': 'data/speech_commands/backward/03401e93_nohash_0.wav', 'array': array([0.00177002, 0.00177002, 0.00177002, ..., 0.00521851, 0.00408936,
       0.00286865]), 'sampling_rate': 16000}, 'label': 'backward'}
{'Unnamed: 0': 0, 'path': {'path': 'data/speech_commands/backward/0165e0e8_nohash_0.wav', 'array': array([-0.06576538, -0.07092285, -0.07531738, ..., -0.06997681,
       -0.07305908, -0.07043457]), 'sampling_rate': 16000}, 'label': 'backward'}


#### 3. Upload the datasets to HF

In [4]:
for split, dataset in datasets.items():
    dataset.push_to_hub('DBD-research-group/beans_sc', split=split)

Uploading the dataset shards:   0%|          | 0/6 [00:00<?, ?it/s]

Map:   0%|          | 0/14141 [00:00<?, ? examples/s]

Creating parquet from Arrow format:   0%|          | 0/142 [00:00<?, ?ba/s]

Map:   0%|          | 0/14141 [00:00<?, ? examples/s]

Creating parquet from Arrow format:   0%|          | 0/142 [00:00<?, ?ba/s]

...

README.md:   0%|          | 0.00/472 [00:00<?, ?B/s]

Uploading the dataset shards:   0%|          | 0/1 [00:00<?, ?it/s]

Map:   0%|          | 0/849 [00:00<?, ? examples/s]

Creating parquet from Arrow format:   0%|          | 0/9 [00:00<?, ?ba/s]

README.md:   0%|          | 0.00/579 [00:00<?, ?B/s]

---
# Download the dataset from HF

Download all splits from the hub. Even when specifying a specific split it still downloads everything! Use `streaming=True` and `cache_dir='...'` for shorter loading times.

In [5]:
from datasets import load_dataset, DatasetDict

#dataset = load_dataset(path='DBD-research-group/beans_sc', split='train_low')
dataset: DatasetDict = load_dataset(name='default', path='DBD-research-group/beans_sc')

Generating train split:   0%|          | 0/84843 [00:00<?, ? examples/s]

Generating valid split:   0%|          | 0/9981 [00:00<?, ? examples/s]

Generating test split:   0%|          | 0/11005 [00:00<?, ? examples/s]

Generating train_low split:   0%|          | 0/849 [00:00<?, ? examples/s]

In [6]:
# print number of samples and number of distinct classes
print(f"Number of samples: {len(dataset['train'])}")
print(f"Number of distinct classes: {len(dataset['train'].unique('label'))}")
dataset

Number of samples: 84843
Number of distinct classes: 35


DatasetDict({
    train: Dataset({
        features: ['Unnamed: 0', 'path', 'label'],
        num_rows: 84843
    })
    valid: Dataset({
        features: ['Unnamed: 0', 'path', 'label'],
        num_rows: 9981
    })
    test: Dataset({
        features: ['Unnamed: 0', 'path', 'label'],
        num_rows: 11005
    })
    train_low: Dataset({
        features: ['Unnamed: 0', 'path', 'label'],
        num_rows: 849
    })
})